# Levy Flights
Goal: attempt implementation of Levy flight so I can apply it to Cuckoo Search

Levy distribution
- [Levy Distribution Theory](https://www.sciencedirect.com/topics/computer-science/levy-distribution)

- [Implementation Source (Matlab)](https://citeseerx.ist.psu.edu/document?repid=rep1&type=pdf&doi=6cca8bc82c0fe24f3af9da54b5b88dcf9ae043c1)

Matplotlib
- [Matplotlib animation example](https://colab.research.google.com/drive/1Ofuol9wHBJKxZlDS4foZ3cm9G8fArOow#scrollTo=rd6h4K9vOtZk)

In [ ]:
from matplotlib import rc
rc('animation', html='jshtml') # for Colab

import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
import scipy.stats as stats
from scipy.special import gamma
from mpl_toolkits import mplot3d # matplotlib addon

from itertools import count # not necessary

In [ ]:
def brownian(mu, sigma):
  return np.random.normal(mu, sigma)

## Mantegna algorithm
1. Step 1. Calculate $v=\frac{x}{|y|^{1/a}}$, where x,y are normally distributed stochastic variables (np.random.normal or Box-Muller/Polar Marsaglia for C++)
2. Step 2 (plug in to step 1): Calculate standard error of stochastic RV's x,y
- $\sigma_x(\alpha) = \left[\frac{\Gamma(1+\alpha)\sin(\pi\alpha/2)}{\Gamma\left((1+\alpha/2\alpha2^{\alpha-1/2}\right)}\right]^{1/\alpha}$
- $\sigma_y=1$

**NOTE:** $\Gamma(\cdot)$ refers to Gamma function (also part of std in cpp via \<algorithm\>)

Nonlinear transformation:
$$w=\left\{\left[K(\alpha) - 1\right] e^{-|v|/C(\alpha)}+1\right\}v$$

Apply this transformation to flattened vector $\sum_{k=1}^n w_k$
$$z_{cn} = \frac{1}{n^{1/\alpha}}\sum_{k=1}^n w_k$$

$K(\alpha)$ (obtained analytically)
$$K(\alpha) = \frac{\alpha\Gamma \left((\alpha+1)/2\alpha\right)}{\Gamma(1/\alpha)} \left[\frac{\alpha\Gamma\left((\alpha+1)/2\right)}{\Gamma(\alpha+1)\sin(\pi\alpha/2)}\right]^{1/\alpha}$$

$C(\alpha)$ comes from a polynomial fit (I'm assuming least squared but idk), from integral
$$\frac{1}{\pi \sigma_x}\int_0^\infty q^{1/\alpha} \exp\left[-\frac{q^2}{2}-\frac{q^{2/a}C(\alpha)^2}{2\sigma_X^2 (\alpha)}\right]dq = \frac{1}{\pi}\int_0^\infty \cos \left[\left(\frac{K(\alpha)-1}{e} + 1\right)C(\alpha)\right]\exp(-q^\alpha) dq$$
- I have no clue how we got this integral for $C(\alpha)$ or analytical solution for $K(\alpha)$

Final RV (returned from function)
$$z=c^{1/\alpha} z_cn$$

In [ ]:
def mantegna(alpha, c, n, N):
  '''
  alpha: parameter \in [0.3, 1.99]. Lower alpha -> heavier tails, meaning more frequent large jumps
  - The higher the alpha is, the more it resembles a normal/Gaussian distribution
  - In other words, tunes the probability of large jumps
  c: parameter (>0). Scaling factor for jumps
  n: number of iterations
  N: number of random samples per iteration/trial
  '''
  if alpha < 0.3 or alpha > 1.99:
    raise ValueError("alpha must be between 0.3 and 1.99")

  if c <= 0:
    raise ValueError("c must be positive")

  if n <= 1:
    raise ValueError("n must be positive")

  if N <= 0:
    raise ValueError("N must be positive")
  # matlab implementation mentions if nargin <4: N = 1???
  if N <= 0:
    raise ValueError("N must be positive")

  invalpha = 1/alpha
  # calculate sigma_x, which should be standard error for nomrally distributed RV x
  sig_x = ((gamma(1+alpha) * np.sin(np.pi * alpha/2)) / (gamma((1+alpha)/2) * alpha *(2**((alpha-1)/2))))** invalpha
  # x is rand matrix times sig_x, y is rand matrix times sig_y = 1, so just rand matrix
  X = np.random.normal(0,1, (n, N))
  Y = np.random.normal(0,1, (n, N))

  v = sig_x * (np.divide(X, (np.abs(Y)** invalpha)))
  # Calculate Kappa(alpha)
  kappa = (alpha * gamma((alpha + 1)/ (2* alpha))) / gamma(invalpha) * \
    ((alpha * gamma((alpha + 1) / 2))/ (gamma(1 + alpha) * np.sin(np.pi * alpha/2)))

  # These coefficients came from polynomial fit of some janky equation. Not strictly necessary to have C
  p = [-17.7767, 113.3855, -281.5879, 337.5439, -193.5494, 44.8754]
  C = np.polyval(p, alpha)
  w = ((kappa-1) * np.exp(-np.abs(v)/C) + 1) * v

  if n > 1:
    z = (1/(n**invalpha)) * np.sum(w, axis = 0)
  else:
    z = w

  z = c**invalpha * z
  # return single generated Levy process number
  return z[0]

In [ ]:
levy_step = mantegna(alpha = 0.5, c = 0.05, n = 10, N = 1)
brownian_step = brownian(mu = 0, sigma = 1)
print(f"Levy step: {levy_step:.3f}")
print(f"Brownian step: {brownian_step:.3f}")


Levy step: -0.004
Brownian step: -2.339


In [ ]:
fig = plt.figure()
ax = plt.axes(projection='3d')

N = 10

# gen random starting point via vector
x=200*np.random.random(N)
y=200*np.random.random(N)
z=200*np.random.random(N)

<IPython.core.display.Javascript object>

In [ ]:
def update(x):
  for i in range(N):
    x[i] += brownian(0,1) + 50 * mantegna(alpha=0.3, c = 0.001, n=10,  N=1)

In [ ]:
def frame(w):
  ax.clear()
  global x,y,z
  update(x)
  update(y)
  update(z)

  plt.title("Levy Flight")
  ax.set_xlabel('x')
  ax.set_ylabel('y')
  ax.set_zlabel('z')

  ax.set_xlim(-500, 500)
  ax.set_ylim(-500, 500)
  ax.set_zlim(-500, 500)

  plot = ax.scatter3D(x, y, z, c=z, cmap='Greens');
  return plot

In [ ]:
anim = FuncAnimation(fig, frame, frames=100, blit=False, repeat = True)

In [ ]:
anim

# Cuckoo Search


```
begin
  Objective function f(x), x = (x1, . . . , xd)^T
  Initialize population of n host nests xi (i = 1, 2, . . . , n)
  while stopping criterion is not met
    Get a cuckoo randomly by Levy flights
    Evaluate its fitness Fi
    Choose a nest j among n randomly
    if (Fi > Fj )
      replace j by the new solution
    end
    A fraction (pa) of worse nests are abandoned and replaced by new ones
    Rank solutions and find the current best
    end while
    Postprocess results and visualization
end
```
Evaluate fitness based on objective function

[Example Cuckoo Search Implementation here](https://github.com/BrianMburu/Cockoo-Search-Algorithm/blob/master/cuckoo_search.py)

[Paper 1](https://www.cs.tufts.edu/comp/150GA/homeworks/hw3/_reading7%20Cuckoo%20search.pdf)

[Paper 2](https://arxiv.org/pdf/1507.08937)

[YT vid](https://www.youtube.com/watch?v=Kn1CrKDZqn8)

# TODO: Change parameter clamping later, fit to heston model

In [ ]:
class CuckooSearch:
  def __init__(self, n, replacement_rate, dim, max_iter, pop_size):
    self.nests = [] * n
    self.best_nest = None
    self.best_fitness = float('inf')
    self.p_a = replacement_rate
    self.dim = dim
    self.max_iter = max_iter
    self.pop_size = pop_size
    self.population = np.random.uniform(-5, 5, (pop_size, dim)) # change these numbers later
    self.initial_fitness = [] * pop_size

    pass

  def objective_function(self, x):
    return np.sum(x**2)

  def levy(self, alpha, c, n, N):
    return mantegna(alpha, c, n, N)

  def main(self):
    self.fitness = np.array([self.objective_function(nest) for nest in population])

    for i in range(self.max_iter):
      # generate new solution by Levy flight
      new_pop = np.empty_like(self.population)

      for j, nest in enumerate(self.population):
        step_size = self.levy(alpha = 0.5, c = 0.001, n = 10, N = 1)
        step_direction = np.random.uniform(-1, 1, self.dim)
        new_nest = nest + step_size * step_direction
        new_pop[j] = new_nest

        # check bounds
        new_pop[j] = np.clip(new_pop[j], -5, 5)

      new_fitness = np.array([self.objective_function(nest) for nest in new_pop])

      # replace population
      best_nest_idx = np.argmin(new_fitness)
      best_nest = new_pop[best_nest_idx]
      best_fitness = new_fitness[best_nest_idx]

      sorted_nests = np.argsort(self.fitness)
      self.population = self.population[sorted_nests]
      self.fitness = self.fitness[sorted_nests]

      if self.fitness < self.best_fitness:
        self.best_nest = self.population[0]
        self.best_fitness = self.fitness[0]

      # Abandon egg with probability pa and lay new eggs. here it seems like we just kick the lowest fitness ones
      abandoned_egg = int(self.p_a * self.pop_size)
      self.population[:abandoned_egg] = np.random.uniform(-5, 5, (abandoned_egg, self.dim))
      self.fitness[:abandoned_egg] = np.array([self.objective_function(nest) for nest in self.population[:abandoned_egg]])

      print(f"Iteration {i+1}: Best fitness = {self.best_fitness}")

    return self.best_nest, self.best_fitness

